# Pretraining
A pretrained model is used to speed up the training, which was necessary for the short time allowed for the research. The pretrained model is created by training for 200 epochs on the pretrain set. To begin we create a run-folder for the pretrain2 and pretrain8 set.

In [2]:
import os
# os.makedirs('KITTI/yolo2/clients/run-pretrain2/')
# os.makedirs('KITTI/yolo8/clients/run-pretrain8/')

In this case we train centralized, i.e. on one device: device 0. Device 0 gets all pretrain samples as labeled samples.

In [2]:
from shutil import copyfile
copyfile('KITTI/yolo2/pretrain.txt', 'KITTI/yolo2/clients/run-pretrain2/l-0.txt')
copyfile('KITTI/yolo8/pretrain.txt', 'KITTI/yolo8/clients/run-pretrain8/l-0.txt')

'KITTI/yolo8/clients/run-pretrain8/l-0.txt'

Start the training on each of the pretrainsets for 200 epochs.

In [1]:
!python research.py --action train --epochs 200 --pretrain --client 0 --classes 2 --round 0 --test --name pretrain2

^C


In [ ]:
!python research.py --action train --epochs 20 --pretrain --client 0 --classes 8 --round 0 --test --name pretrain8

And copy them to an easily accessible location

In [ ]:
copyfile('runs/run-pretrain2-0-0/weights/last.pt', 'startingpoint.pt')
copyfile('runs/run-pretrain8-0-0/weights/last.pt', 'startingpoint8.pt')

# Experiments
## Introduction
The algorithm consists of multiple steps: an active learning step, a training step and a federated learning step. These have been defined in the research.py files. These steps can be combined in multiple ways, with different parameters to create the runs described in the paper. Each of the runs has a numbered identifier, a mapping from numbered identifier to the name in the paper will be provided later. 
#### Process spawning
In this notebook we assume that for every step of the algorithm we start a new process. This is done since python does not clear up the memory (well enough) after a training iteration (committed memory remains high, sometimes graphics memory is not emptied). Forcing the garbage collector only results in marginable returns. Therefore a new process for each step is chosen, as after the step finishes, the entire memory used by the process is forcefully cleared by the OS. 

Note: this adds additional overhead, plus in rounds the datasets are often reinitialized. If one has the memory available, the simple modification can be made which selects the dataloader from a pre-initialized pool of dataloaders depending on the device ID in start_training in research.py. One can then just call research.py for every round or make the necessary loops in research.py. Warning: this can take excessive amounts of memory and is thus prone to crashes, and can additionally only be used after the datasets for each device are constant, i.e. after AL iterations have finished. Speedups can be expected as 15-20 seconds per device per round.

### Initializing Step
To begin with the experiments for a run, we initialize the device files. That means creating the necessary directories and adding all device files to its unlabeled datapool. This is done as follows:

In [2]:
!python research.py --action init --classes 2 --name example 

### Active learning step
With the folders created, we can begin by using AL for the pretrained starting point weights. The active learning aggregation method and samples can be defined through parameters. The client parameter indicates the device on which the active learning step is executed. The active learning step will only use the data available on that device.

In [ ]:
!python research.py --action al --al_method sum --weights startingpoint.pt --client 0 --classes 2 --round 0 --name example 

### Training step
Now that files are labelled on the device, we can begin training. The training code is based on the PyTorch YOLOv5 implementation, adapted specifically for this paper. The original code can be seen at: https://github.com/ultralytics/yolov5. 
In chained methods, we use the freeze_backbone parameter during training.

In [ ]:
!python research.py --action train --epochs 20 --weights startingpoint.pt --client 0 --classes 2 --round 0 --name example 

### FedAvg step
After multiple devices have finished training, we can fedavg the resulting checkpoints, to recreate pseudo-FL.


In [ ]:
!python research.py --action fedavg --classes 2 --round 0 --name example 

### Composing
These steps can now be combined in a for-loop using iPython, e.g. as follows:

In [ ]:
# Initialize run
!python research.py --action init --classes 2 --name example1 

In [ ]:
# First round is using startingpoint.pt, after that we reuse weights in all other rounds. (When FedAvg'ing)
for client in range(0, 9):
    !python research.py --action al --al_method sum --weights startingpoint.pt --client {client} --classes 2 --round 0 --name example1 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name example1 
!python research.py --action fedavg --classes 2 --round 0 --name example1

In [ ]:
# The Active Learning rounds
for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method sum --reuse_weights --client {client} --classes 2 --round {curr_round} --name example1 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name example1 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name example1

In [ ]:
# The non-active learning rounds. 
# These are the rounds you can optimize by reusing the dataloaders for each device through a pooled dataloader.
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name example1 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name example1

# Executing the experiments described in the paper
These are the experiments described in the paper. The names in the paper were given after the runs were completed. The original names for the runs are numbered.

A small sidenote: much of the experiments here were executed in different python notebooks. For the repository these notebooks have been aggregated into one large codebase with flags for each of the runs. This is done to allow reviewers and contributors to more easily understand the code (rather than searching endlessly through 39 python notebooks). It is recommended to run the code below in different notebooks as well, as the logging output will often result in a python notebook in the hundreds of megabytes. This makes it incredibly slow to load the notebook.

It can occur that a slightly different AL sample is selected in one run, compared to another run. This happens if the confidences are very close and the model training has slightly different weights (which can happen as SGD optimizer uses randomness). The randomness is seeded, however it appears PyTorch internally uses an unseeded random generator. The influence of this should be negligible. The originally selected AL samples and resulting weights are kept by the author for reproducability. Due to the size (more than 200GB) these cannot be uploaded to this repository, but are available via the emailadress in the paper. 

## FedAvg runs

### 2-2*-SUM (Run-4)

In [ ]:
!python research.py --action init --classes 2 --name 4 

for client in range(0, 9):
    !python research.py --action al --al_method sum --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 4 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 4 
!python research.py --action fedavg --classes 2 --round 0 --name 4

for curr_round in range(1,22):
    for client in range(0, 9):
        weights = f'runs/run-4-{client}-{curr_round -1}'
        !python research.py --action al --al_method sum --weights {weights} --client {client} --classes 2 --round {curr_round} --name 4 
        !python research.py --action train --epochs 20 --weights {weights} --client {client} --classes 2 --round {curr_round} --name 4 
!python research.py --action fedavg --classes 2 --round 21 --name 4
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 4 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 4

### -> 2-2*-AVG (Run-4a)

In [ ]:
!python research.py --action init --classes 2 --name 4a 

for client in range(0, 9):
    !python research.py --action al --al_method avg --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 4a 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 4a 
!python research.py --action fedavg --classes 2 --round 0 --name 4a

for curr_round in range(1,22):
    for client in range(0, 9):
        weights = f'runs/run-4a-{client}-{curr_round -1}/weights/last.pt'
        !python research.py --action al --al_method avg --weights {weights} --client {client} --classes 2 --round {curr_round} --name 4a 
        !python research.py --action train --epochs 20 --weights {weights} --client {client} --classes 2 --round {curr_round} --name 4a 
!python research.py --action fedavg --classes 2 --round 21 --name 4a
    
for curr_round in range(22,201):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 4a 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 4a

### -> 2-2*-MAX (Run-4b)

In [ ]:
!python research.py --action init --classes 2 --name 4b

for client in range(0, 9):
    !python research.py --action al --al_method max --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 4b 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 4b 
!python research.py --action fedavg --classes 2 --round 0 --name 4b

for curr_round in range(1,22):
    for client in range(0, 9):
        weights = f'runs/run-4b-{client}-{curr_round -1}/weights/last.pt'
        !python research.py --action al --al_method max --weights {weights} --client {client} --classes 2 --round {curr_round} --name 4b 
        !python research.py --action train --epochs 20 --weights {weights} --client {client} --classes 2 --round {curr_round} --name 4b 
!python research.py --action fedavg --classes 2 --round 21 --name 4b
    
for curr_round in range(22,201):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 4b 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 4b

### 2-2*-RND (Run-5)

In [ ]:
!python research.py --action init --classes 2 --name 5 

for client in range(0, 9):
    !python research.py --action al --al_method rnd --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 5 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 5 
!python research.py --action fedavg --classes 2 --round 0 --name 5

for curr_round in range(1,22):
    for client in range(0, 9):
        weights = f'runs/run-5-{client}-{curr_round -1}/weights/last.pt'
        !python research.py --action al --al_method rnd --weights {weights} --client {client} --classes 2 --round {curr_round} --name 5 
        !python research.py --action train --epochs 20 --weights {weights} --client {client} --classes 2 --round {curr_round} --name 5 
!python research.py --action fedavg --classes 2 --round 21 --name 5
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 5 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 5

### 2-2-AVG (Run-8)

In [ ]:
!python research.py --action init --classes 2 --name 8 

for client in range(0, 9):
    !python research.py --action al --al_method rnd --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 8 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 8 
!python research.py --action fedavg --classes 2 --round 0 --name 8

for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method rnd --reuse_weights --client {client} --classes 2 --round {curr_round} --name 8 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 8 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 8
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 8 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 8

### 2-2-SUM (Run-10)

In [ ]:
!python research.py --action init --classes 2 --name 10 

for client in range(0, 9):
    !python research.py --action al --al_method sum --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 10 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 10 
!python research.py --action fedavg --classes 2 --round 0 --name 10

for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method sum --reuse_weights --client {client} --classes 2 --round {curr_round} --name 10 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 10 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 10
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 10 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 10

### 2-2-AVG (Run-11)

In [ ]:
!python research.py --action init --classes 2 --name 11 

for client in range(0, 9):
    !python research.py --action al --al_method avg --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 11 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 11 
!python research.py --action fedavg --classes 2 --round 0 --name 11

for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method avg --reuse_weights --client {client} --classes 2 --round {curr_round} --name 11 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 11 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 11
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 11 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 11

### 2-2-MAX (Run-12)

In [ ]:
!python research.py --action init --classes 2 --name 12 

for client in range(0, 9):
    !python research.py --action al --al_method max --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 12 
    !python research.py --action train --epochs 20 --weights startingpoint.pt --client {client} --classes 2 --round 0 --name 12 
!python research.py --action fedavg --classes 2 --round 0 --name 12

for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method max --reuse_weights --client {client} --classes 2 --round {curr_round} --name 12 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 12
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 12
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 12 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 12

In [ ]:
for curr_round in range(111,201):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 12 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 12

In [ ]:
curr_round = 122
for client in range(5, 9):
    !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 12 
!python research.py --action fedavg --classes 2 --round {curr_round} --name 12
for curr_round in range(123,201):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 12 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 12

In [ ]:
for curr_round in range(201,300):
    for client in range(0, 9):
        !python research.py --action train --epochs 2 --reuse_weights --client {client} --classes 2 --round {curr_round} --name 12 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name 12

### 8-2-MAX (Run-14)

In [ ]:
!python research.py --action init --classes 8 --name 14 

for client in range(0, 9):
    !python research.py --action al --al_method max --weights startingpoint8.pt --client {client} --classes 8 --round 0 --name 14 
    !python research.py --action train --epochs 20 --weights startingpoint8.pt --client {client} --classes 8 --round 0 --name 14 
!python research.py --action fedavg --classes 8 --round 0 --name 14

for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method max --reuse_weights --client {client} --classes 8 --round {curr_round} --name 14 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 8 --round {curr_round} --name 14 
    !python research.py --action fedavg --classes 8 --round {curr_round} --name 14
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 8 --round {curr_round} --name 14 
    !python research.py --action fedavg --classes 8 --round {curr_round} --name 14

### 8-2-RND (Run-16)


In [ ]:
!python research.py --action init --classes 8 --name 16 

for client in range(0, 9):
    !python research.py --action al --al_method rnd --weights startingpoint8.pt --client {client} --classes 8 --round 0 --name 16 
    !python research.py --action train --epochs 20 --weights startingpoint8.pt --client {client} --classes 8 --round 0 --name 16 
!python research.py --action fedavg --classes 8 --round 0 --name 16

for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method rnd --reuse_weights --client {client} --classes 8 --round {curr_round} --name 16 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 8 --round {curr_round} --name 16 
    !python research.py --action fedavg --classes 8 --round {curr_round} --name 16
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 8 --round {curr_round} --name 16 
    !python research.py --action fedavg --classes 8 --round {curr_round} --name 16

### 8-2-SUM (Run-17)

In [ ]:
!python research.py --action init --classes 8 --name 17

for client in range(0, 9):
    !python research.py --action al --al_method sum --weights startingpoint8.pt --client {client} --classes 8 --round 0 --name 17 
    !python research.py --action train --epochs 20 --weights startingpoint8.pt --client {client} --classes 8 --round 0 --name 17 
!python research.py --action fedavg --classes 8 --round 0 --name 17

for curr_round in range(1,22):
    for client in range(0, 9):
        !python research.py --action al --al_method sum --reuse_weights --client {client} --classes 8 --round {curr_round} --name 17 
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 8 --round {curr_round} --name 17 
    !python research.py --action fedavg --classes 8 --round {curr_round} --name 14
    
for curr_round in range(22,111):
    for client in range(0, 9):
        !python research.py --action train --epochs 20 --reuse_weights --client {client} --classes 8 --round {curr_round} --name 17 
    !python research.py --action fedavg --classes 8 --round {curr_round} --name 17

Loaded 580 unlabelled files, which will be labelled through active learning
Labelled 10/10 unlabelled files
Reflected AL step in ul and labelled set files


C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]


^C
^C


## The chained runs
### 2-Chained (Run-Chainx)

In [ ]:
!python research.py --action aggchain --classes 2 --round 0 --name Chainx # save agg to pseudo_fl/chainagg.pt


In [ ]:
!python research.py --action init --classes 2 --name Chainx 

for client in range(0, 9):
    if client == 0:
        weights = 'startingpoint.pt'
    else:
        weights = f'runs/run-Chainx-{client-1}-0'
    !python research.py --action al --al_method sum --al_samples 220 --weights {weights} --client {client} --classes 2 --round 0 --name Chainx 
    !python research.py --action train --epochs 200 --weights {weights} --client {client} --classes 2 --round 0 --test --name Chainx 
!python research.py --action aggchain --classes 2 --round 0 --name Chainx -aggr_metric ap50 
# saved agg to pseudo_fl/chainagg.pt

for curr_round in range(1,21):
    for client in range(0, 9):
        if client == 0 and curr_round == 1:
            weights = 'pseudo_fl/Chainxagg.pt'
        elif client == 0:
            weights = f'runs/run-Chainx-8-{curr_round -1}'
        else:
            weights = f'runs/run-Chainx-{client -1}-{curr_round}'
        !python research.py --action train --epochs 20 --weights {weights} --freeze-backbone --client {client} --classes 2 --round {curr_round} --name Chainx 

### 2-Chained-Fed-Avg (Run-CFed)

In [ ]:
!python research.py --action init --classes 2 --name CFed
# First round from chainagg.pt, shared with Run-Chainx
for client in range(0, 9):
      !python research.py --action train --epochs 20 --weights pseudo_fl/Chainxagg.pt --freeze-backbone --client {client} --classes 2 --round 1 --name CFed 
!python research.py --action fedavg --classes 2 --round 1 --name CFed

# Rounds after that in regular fedavg fashion with reuse_weights.
for curr_round in range(2,21):
    for client in range(0, 9):
          !python research.py --action train --epochs 20 --reuse_weights --freeze-backbone --client {client} --classes 2 --round {curr_round} --name CFed 
    !python research.py --action fedavg --classes 2 --round {curr_round} --name CFed

### 8-Chained (Run-15x)

In [ ]:
!python research.py --action init --classes 8 --name 15x 

for client in range(0, 9):
    if client == 0:
        weights = 'startingpoint8.pt'
    else:
        weights = f'runs/run-15x-{client-1}-0'
    !python research.py --action al --al_method sum --al_samples 220 --weights {weights} --client {client} --classes 8 --round 0 --name 15x 
    !python research.py --action train --epochs 200 --weights {weights} --client {client} --classes 8 --round 0 --test --name 15x 
!python research.py --action aggchain --classes 8 --round 0 --name 15x # save agg to pseudo_fl/chainagg.pt

for curr_round in range(1,21):
    for client in range(0, 9):
        if client == 0 and curr_round == 1:
            weights = 'pseudo_fl/15xagg.pt'
        elif client == 0:
            weights = f'runs/run-15x-8-{curr_round -1}'
        else:
            weights = f'runs/run-15x-{client -1}-{curr_round}'
        !python research.py --action train --epochs 20 --weights {weights} --freeze-backbone --client {client} --classes 8 --round {curr_round} --name 15x 

## The centralized runs
To create the run files for the centralized baseline, we take everything in the labelled sets of all devices for one run, and store it in one file on one device.

In [ ]:
def create_centralized_run_files(name, nc):
    total_images = []
    for file in glob.glob(f"KITTI/yolo{nc}/clients/run-{name}/l-*.txt"): 
        with open(file, "r") as f:
            for line in f.readlines():
                total_images.append(line.replace('\n',''))
    os.makedirs(f"KITTI/yolo{nc}/clients/run-{name}-CENTRALIZED/)
    with open(f"KITTI/yolo{nc}/clients/run-{name}-CENTRALIZED/l-0.txt", "w") as f:
        for line in total_images:
            f.write(line+'\n')

With those files, a model is trained from scratch for 200 epochs. The number of classes has to be known per run, so this is manually entered in a mapping.

In [ ]:
run_classes_mapping = {'4': 2, '5': 2, '8': 2, '10': 2, '11': 2, '12': 2, '14': 8, '16': 8, 'Chainx': 2, 'CFed': 2, '15x': 8}
for name, nc in d.items():
    create_centralized_run_files(name, nc)
    !python research.py --action train --epochs 200 --pretrain --client 0 --classes {nc} --round 0 --test --name {name+"-CENTRALIZED"} 

# FL vs CL

In [1]:
PRETRAIN_SET = 200
DEVICES = 4
import evaluate
import torch
from utils.datasets import create_dataloader
import os
from shutil import copyfile
# model = torch.load("pretrain_20ep_4batches_CL.pt",map_location=torch.device)
# model.float().state_dict()
# class opt: pass
# opt.single_cls = False
# dl = create_dataloader(f'KITTI/flcl/val.txt', 640, 4, 32, opt, pad=0.5, rect=True, prefix=colorstr('val2: '))[0]
# res, maps, t, a = evaluate(model)

In [2]:
def create_dir_ds(cl_name, fl_name):
    os.makedirs('KITTI/flcl/clients/run-'+cl_name+'/')
    copyfile('KITTI/flcl/cl.txt', 'KITTI/flcl/clients/run-'+cl_name+'/l-0.txt')
    os.makedirs('KITTI/flcl/clients/run-'+fl_name+'/')
    copyfile('KITTI/flcl/clients/0.txt', 'KITTI/flcl/clients/run-'+fl_name+'/l-0.txt')
    copyfile('KITTI/flcl/clients/1.txt', 'KITTI/flcl/clients/run-'+fl_name+'/l-1.txt')
    copyfile('KITTI/flcl/clients/2.txt', 'KITTI/flcl/clients/run-'+fl_name+'/l-2.txt')
    copyfile('KITTI/flcl/clients/3.txt', 'KITTI/flcl/clients/run-'+fl_name+'/l-3.txt')

In [11]:
cl_name = "cl-rerun-m15"
fl_name = "fl-rerun-m15"

In [12]:
create_dir_ds(cl_name,fl_name)

In [14]:
os.makedirs('KITTI/flcl/clients/run-cl-trial-m15/')

In [15]:
os.makedirs('KITTI/flcl/clients/run-fl-trial-m15/')

In [16]:
# from shutil import copyfile
copyfile('KITTI/flcl/clients/0.txt', 'KITTI/flcl/clients/run-fl-trial-m15/l-0.txt')
copyfile('KITTI/flcl/clients/1.txt', 'KITTI/flcl/clients/run-fl-trial-m15/l-1.txt')
copyfile('KITTI/flcl/clients/2.txt', 'KITTI/flcl/clients/run-fl-trial-m15/l-2.txt')
copyfile('KITTI/flcl/clients/3.txt', 'KITTI/flcl/clients/run-fl-trial-m15/l-3.txt')

'KITTI/flcl/clients/run-fl-trial/l-3.txt'

In [17]:
copyfile('KITTI/flcl/cl.txt', 'KITTI/flcl/clients/run-cl-trial-m15/l-0.txt')

'KITTI/flcl/clients/run-cl-trial/l-0.txt'

In [6]:
round_mapping = {}
for rd in range(20):
    if rd == 0:
        rd_x = rd
        round_mapping[rd] = f'{rd_x}'
    else:
        rd_x = rd+1
        round_mapping[rd] = f'{rd_x:02d}'

In [7]:
round_mapping

{0: '0',
 1: '02',
 2: '03',
 3: '04',
 4: '05',
 5: '06',
 6: '07',
 7: '08',
 8: '09',
 9: '10',
 10: '11',
 11: '12',
 12: '13',
 13: '14',
 14: '15',
 15: '16',
 16: '17',
 17: '18',
 18: '19',
 19: '20'}

In [8]:
for rd in range(20):
    for client in range(DEVICES):
        if client == 0 and rd == 0:
            weights = 'pretrain_20ep_4batches_CL.pt'
        elif client == 0:
            weights = f'runs/run-flcl-fl-3-{round_mapping[rd-1]}/weights/last.pt'
        else:
            weights = f'runs/run-flcl-fl-{client-1}-{round_mapping[rd]}/weights/last.pt'
        !python research2.py --action train --epochs 1 --batch_size 1 --weights {weights} --client {client} --classes 8 --round 0 --test --name flcl-fl

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.78, Best Possible Recall (BPR) = 0.9967
                 all        2244       12341      0.0101      0.0165     0.00486     0.00102
                 car        2244        8748      0.0812       0.132      0.0383     0.00804
             cyclist        2244         496           0           0           0           0
                misc        2244         293           0           0    7.38e-06    1.69e-06
          pedestrian        2244        1332           0           0    5.62e-07    1.83e-07
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0     1.3e-05       3e-06
                 van        2244         905           0           0    0.000518    8.25e-05
Optimizer stripped from runs\r

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]
     

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  67%|######6   | 751/1122 [00:42<00:19, 19.07it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  67%|######7   | 753/1122 [00:42<00:19, 18.93it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  67%|######7   | 755/1122 [00:42<00:19, 18.68it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  68%|######7   | 758/1122 [00:42<00:18, 19.22it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  68%|######7   | 761/1122 [00:42<00:18, 19.61it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  68%|######8   | 763/1122 [00:42<00:18, 19.29it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  68%|######8   | 765/1122 [00:42<00:

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.62, Best Possible Recall (BPR) = 1.0000
                 all        2244       12341    0.000506      0.0286    0.000102    1.63e-05
                 car        2244        8748     0.00392       0.148    0.000802    0.000128
             cyclist        2244         496    0.000121      0.0806    1.42e-05    2.63e-06
                misc        2244         293           0           0           0           0
          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0           0
                 van        2244         905           0           0           0           0
Optimizer stripped from runs\r

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl\l-1.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl\l-1.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]
     

...

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  15%|#5        | 171/1122 [00:12<01:23, 11.42it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  15%|#5        | 173/1122 [00:12<01:20, 11.74it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  16%|#5        | 175/1122 [00:12<01:18, 12.01it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  16%|#5        | 177/1122 [00:12<01:19, 11.95it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  16%|#5        | 179/1122 [00:13<01:20, 11.78it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  16%|#6        | 181/1122 [00:13<01:18, 11.96it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  16%|#6        | 183/1122 [00:13<01:

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.78, Best Possible Recall (BPR) = 0.9967
                 all        2244       12341    0.000515      0.0287    0.000105     1.7e-05
                 car        2244        8748       0.004       0.151    0.000825    0.000134
             cyclist        2244         496    0.000118      0.0786    1.27e-05    2.11e-06
                misc        2244         293           0           0           0           0
          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0           0
                 van        2244         905           0           0           0           0
Optimizer stripped from runs\r

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]
     

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  36%|###6      | 409/1122 [00:27<00:47, 15.08it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  37%|###6      | 411/1122 [00:27<00:47, 15.07it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  37%|###6      | 413/1122 [00:27<00:46, 15.20it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  37%|###6      | 415/1122 [00:27<00:48, 14.52it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  37%|###7      | 417/1122 [00:27<00:51, 13.68it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  37%|###7      | 419/1122 [00:27<00:50, 13.95it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  38%|###7      | 421/1122 [00:28<00:

Missing files. Existing are: weights: runs/run-flcl-fl-0-10False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-1-10False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-2-10False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-3-10False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-0-11False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-1-11False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-2-11False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-3-11False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-0-12False, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-flcl-fl-1-12False, model: True, hyperparamet

In [4]:
for client in range(DEVICES):
    if client == 0:
        weights = 'pretrain_20ep_4batches_CL.pt'
    else:
        weights = f'runs/run-flcl-fl-1epoch-nov30-{client-1}-0/weights/last.pt'
    !python research2.py --action train --epochs 1 --batch_size 1 --weights {weights} --client {client} --classes 8 --round 0 --test --name flcl-fl-1epoch-nov30

C:\Experiments\ALFL
C:\Experiments\ALFL



C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-0' images and labels... 21 found, 0 missing, 0 empty, 0 corrupted:  42%|####2     | 21/50 [00:00<00:00, 207.92it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-0' images and labels... 43 found, 0 missing, 0 empty, 0 corrupted:  86%|########6 | 43/50 [00:00<00:00, 213.74it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-0' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 215.52it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

autoanchor: Analyzing anchors... anchors/target = 4.78, Best Possible Recall (BPR) = 0.9967
                 all        2244       12341      0.0102      0.0166     0.00486    0.000993
                 car        2244        8748      0.0813       0.132      0.0383     0.00786
             cyclist        2244         496           0           0           0           0
                misc        2244         293           0           0    7.38e-06    1.69e-06
          pedestrian        2244        1332           0           0    5.61e-07    1.83e-07
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0     1.3e-05       3e-06
                 van        2244         905           0           0    0.000528    8.52e-05
Optimizer stripped from runs\run-flcl-fl-1epoch-nov30-0-0\weights\last.

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  34%|###3      | 376/1122 [00:20<00:36, 20.33it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  34%|###3      | 379/1122 [00:20<00:35, 20.77it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  34%|###4      | 382/1122 [00:20<00:36, 20.47it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  34%|###4      | 385/1122 [00:20<00:36, 20.11it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  35%|###4      | 388/1122 [00:21<00:35, 20.41it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  35%|###4      | 391/1122 [00:21<00:35, 20.71it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  35%|###5      | 394/1122 [00:21<00:

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-1' images and labels... 14 found, 0 missing, 0 empty, 0 corrupted:  28%|##8       | 14/50 [00:00<00:00, 135.93it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-1' images and labels... 31 found, 0 missing, 0 empty, 0 corrupted:  62%|######2   | 31/50 [00:00<00:00, 151.33it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-1' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 163.40it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

...

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-2' images and labels... 16 found, 0 missing, 0 empty, 0 corrupted:  32%|###2      | 16/50 [00:00<00:00, 156.86it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-2' images and labels... 34 found, 0 missing, 0 empty, 0 corrupted:  68%|######8   | 34/50 [00:00<00:00, 167.43it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-2' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 167.00it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  69%|######8   | 770/1122 [00:42<00:20, 16.79it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  69%|######8   | 772/1122 [00:42<00:20, 17.07it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  69%|######8   | 774/1122 [00:42<00:20, 16.92it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  69%|######9   | 776/1122 [00:43<00:19, 17.56it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  69%|######9   | 778/1122 [00:43<00:19, 17.42it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  70%|######9   | 780/1122 [00:43<00:19, 17.97it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  70%|######9   | 782/1122 [00:43<00:

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.73, Best Possible Recall (BPR) = 0.9964
                 all        2244       12341     0.00931      0.0117     0.00259    0.000484
                 car        2244        8748      0.0729      0.0864      0.0205     0.00383
             cyclist        2244         496           0           0           0           0
                misc        2244         293     0.00161     0.00683    2.65e-05    7.57e-06
          pedestrian        2244        1332           0           0    2.66e-06    5.52e-07
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0     4.8e-06    6.22e-07
                 van        2244         905           0           0    0.000172    2.92e-05
Optimizer stripped from runs\r

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-3' images and labels... 17 found, 0 missing, 0 empty, 0 corrupted:  34%|###4      | 17/50 [00:00<00:00, 170.00it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-3' images and labels... 34 found, 0 missing, 0 empty, 0 corrupted:  68%|######8   | 34/50 [00:00<00:00, 167.05it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-nov30\l-3' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 173.61it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  42%|####1     | 466/1122 [00:26<00:35, 18.55it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  42%|####1     | 468/1122 [00:27<00:35, 18.40it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  42%|####1     | 470/1122 [00:27<00:35, 18.44it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  42%|####2     | 472/1122 [00:27<00:35, 18.36it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  42%|####2     | 474/1122 [00:27<00:34, 18.56it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  43%|####2     | 477/1122 [00:27<00:34, 18.72it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  43%|####2     | 479/1122 [00:27<00:

In [5]:
!python research2.py --action train --epochs 1 --batch_size 4 --weights {weights} --client {client} --classes 8 --round 0 --test --name flcl-fl-1epoch-nov30

'08'

In [2]:
!python research2.py --action train --epochs 1 --batch_size 4 --pretrain --client 0 --classes 8 --round 0 --test --name flcl-cl-1epoch-feb23

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.79, Best Possible Recall (BPR) = 0.9981
                 all        2244       12341    0.000489      0.0296    7.99e-05    1.26e-05
                 car        2244        8748     0.00377       0.142    0.000624    9.86e-05
             cyclist        2244         496    0.000142      0.0948    1.51e-05    2.41e-06
                misc        2244         293           0           0           0           0
          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0           0
                 van        2244         905           0           0           0           0
Optimizer stripped from runs\r

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/200 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb23\l-0' images and labels... 21 found, 0 missing, 0 empty, 0 corrupted:  10%|#         | 21/200 [00:00<00:00, 201.92it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb23\l-0' images and labels... 43 found, 0 missing, 0 empty, 0 corrupted:  22%|##1       | 43/200 [00:00<00:00, 211.16it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb23\l-0' images and labels... 67 found, 0 missing, 0 empty, 0 corrupted:  34%|###3      | 67/200 [00:00<00:00, 219.23it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb23\l-0' ima

In [8]:
for client in range(DEVICES):
        if client == 0:
            !python research2.py --action train --epochs 1 --batch_size 4 --pretrain --client 0 --classes 8 --round 0 --test --name flcl-cl-1epoch-feb23
        else:
            weights = f'runs/run-Chainx-{client -1}-{curr_round}'
        !python research.py --action train --epochs 20 --weights {weights} --freeze-backbone --client {client} --classes 2 --round {curr_round} --name Chainx 

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.78, Best Possible Recall (BPR) = 0.9967
                 all        2244       12341    0.000515      0.0287    0.000107    1.73e-05
                 car        2244        8748       0.004       0.151    0.000841    0.000137
             cyclist        2244         496    0.000118      0.0786    1.27e-05    2.09e-06
                misc        2244         293           0           0           0           0
          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0           0
                 van        2244         905           0           0           0           0
Optimizer stripped from runs\r

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0

Missing files. Existing are: weights: runs/run-flcl-fl-1epoch-feb23-2-0/weights/best.ptFalse, model: True, hyperparameters: True
C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.62, Best Possible Recall (BPR) = 1.0000
                 all        2244       12341    0.000529      0.0288    0.000256    4.16e-05
                 car        2244        8748     0.00389       0.147     0.00203    0.000329
             cyclist        2244         496    0.000121      0.0806    1.76e-05    3.02e-06
                misc        2244         293           0           0           0           0
          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0       

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-1.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-1.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  18%|#7        | 201/1122 [00:10<00:44, 20.91it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  18%|#8        | 204/1122 [00:10<00:43, 21.06it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  18%|#8        | 207/1122 [00:11<00:43, 21.21it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  19%|#8        | 210/1122 [00:11<00:42, 21.46it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  19%|#8        | 213/1122 [00:11<00:42, 21.50it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  19%|#9        | 216/1122 [00:11<00:41, 21.66it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  20%|#9        | 219/1122 [00:11<00:

...

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-2' images and labels... 18 found, 0 missing, 0 empty, 0 corrupted:  36%|###6      | 18/50 [00:00<00:00, 176.47it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-2' images and labels... 36 found, 0 missing, 0 empty, 0 corrupted:  72%|#######2  | 36/50 [00:00<00:00, 171.52it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-2' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 181.82it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

          pedestrian        2244        1332     0.00228    0.000751    0.000296    8.87e-05
      person_sitting        2244          87           0           0           0           0
                tram        2244         154    0.000165     0.00649     1.9e-06    7.59e-07
               truck        2244         326     0.00154       0.046    0.000292    4.92e-05
                 van        2244         905    0.000184     0.00331     2.3e-06    7.63e-07
Optimizer stripped from runs\run-flcl-fl-1epoch-feb23-2-0\weights\last.pt, 14.4MB
Optimizer stripped from runs\run-flcl-fl-1epoch-feb23-2-0\weights\best.pt, 14.4MB


               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   0%|          | 1/1122 [00:01<20:46,  1.11s/it]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   0%|          | 4/1122 [00:01<04:36,  4.04it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   1%|          | 6/1122 [00:01<03:00,  6.18it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   1%|          | 8/1122 [00:01<02:13,  8.32it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   1%|          | 11/1122 [00:01<01:38, 11.29it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   1%|1         | 14/1122 [00:01<01:19, 13.99it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   2%|1         | 17/1122 [00:01<01:09, 15.92it

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.73, Best Possible Recall (BPR) = 0.9964
                 all        2244       12341     0.00123      0.0248    0.000175    4.66e-05
                 car        2244        8748     0.00723      0.0585    0.000875    0.000147
             cyclist        2244         496    0.000197      0.0101    3.52e-05    9.04e-06
                misc        2244         293    0.000327       0.041    2.64e-05    5.78e-06
          pedestrian        2244        1332    0.000413     0.00976    8.63e-06    1.67e-06
      person_sitting        2244          87    4.68e-05      0.0115    2.65e-05    7.35e-06
                tram        2244         154    4.27e-05     0.00649    3.28e-05    5.05e-06
               truck        2244         326    0.000452      0.0276    4.47e-05    8.49e-06
                 van        2244         905     0.00111      0.0331    0.000355    0.000189
Optimizer stripped from runs\r

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-3' images and labels... 20 found, 0 missing, 0 empty, 0 corrupted:  40%|####      | 20/50 [00:00<00:00, 196.01it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-3' images and labels... 42 found, 0 missing, 0 empty, 0 corrupted:  84%|########4 | 42/50 [00:00<00:00, 207.63it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb23\l-3' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 203.25it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

## Optimizer Stripped - Best.pt

In [7]:
!python research2.py --action train --epochs 1 --batch_size 4 --pretrain --client 0 --classes 8 --round 0 --test --name flcl-cl-1epoch-feb24

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.79, Best Possible Recall (BPR) = 0.9981
                 all        2244       12341    0.000489      0.0296    7.94e-05    1.27e-05
                 car        2244        8748     0.00377       0.142     0.00062    9.93e-05
             cyclist        2244         496    0.000142      0.0948    1.51e-05    2.27e-06
                misc        2244         293           0           0           0           0

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/200 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb24\l-0' images and labels... 22 found, 0 missing, 0 empty, 0 corrupted:  11%|#1        | 22/200 [00:00<00:00, 211.54it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb24\l-0' images and labels... 44 found, 0 missing, 0 empty, 0 corrupted:  22%|##2       | 44/200 [00:00<00:00, 211.54it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb24\l-0' images and labels... 69 found, 0 missing, 0 empty, 0 corrupted:  34%|###4      | 69/200 [00:00<00:00, 226.70it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb24\l-0' ima


          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0           0
                 van        2244         905           0           0           0           0


 80%|########  | 40/50 [00:18<00:03,  3.01it/s]
       0/0    0.845G    0.1173    0.0566   0.06285    0.2368        31       640:  80%|########  | 40/50 [00:19<00:03,  3.01it/s]
 82%|########2 | 41/50 [00:19<00:03,  2.99it/s]
       0/0    0.845G    0.1172   0.05647    0.0628    0.2365        29       640:  82%|########2 | 41/50 [00:19<00:03,  2.99it/s]
 84%|########4 | 42/50 [00:19<00:02,  3.03it/s]
       0/0    0.845G    0.1172   0.05658   0.06278    0.2365        47       640:  84%|########4 | 42/50 [00:19<00:02,  3.03it/s]
 86%|########6 | 43/50 [00:19<00:02,  3.00it/s]
       0/0    0.845G    0.1171   0.05712   0.06275    0.2369        62       640:  86%|########6 | 43/50 [00:19<00:02,  3.00it/s]
 88%|########8 | 44/50 [00:19<00:01,  3.03it/s]
       0/0    0.845G     0.117    0.0575   0.06267    0.2371        54       640:  88%|########8 | 44/50 [00:20<00:01,  3.03it/s]
 90%|######### | 45/50 [00:20<00:01,  3.00it/s]
       0/0    0.845G    0.1169   0.05759   0.06261    0.2371  

In [9]:
for client in range(DEVICES):
        if client == 0:
            !python research2.py --action train --epochs 1 --batch_size 1 --pretrain --client 0 --classes 8 --round 0 --test --name flcl-fl-1epoch-feb24
        else:
            weights = f'runs/run-flcl-fl-{client-1}-0/weights/best.pt'
            !python research2.py --action train --epochs 1 --batch_size 1 --weights {weights} --client {client} --classes 8 --round 0 --test --name flcl-fl-1epoch-feb24 

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.78, Best Possible Recall (BPR) = 0.9967
                 all        2244       12341    0.000516      0.0287    0.000103    1.63e-05
                 car        2244        8748     0.00401       0.151    0.000808    0.000129
             cyclist        2244         496    0.000118      0.0786    1.31e-05     2.1e-06
                misc        2244         293           0           0           0           0
          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0           0
                 van        2244         905           0           0           0           0


C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-0.cache' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.62, Best Possible Recall (BPR) = 1.0000
                 all        2244       12341     0.00967      0.0173     0.00425     0.00083
                 car        2244        8748      0.0759       0.135      0.0336     0.00657
             cyclist        2244         496           0           0           0           0
                misc        2244         293     0.00142     0.00341    1.98e-05    6.14e-06
          pedestrian        2244        1332           0           0    7.76e-07    1.56e-07
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0    1.03e-05    2.02e-06
                 van        2244         905           0           0    0.000408    6.24e-05


C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-1' images and labels... 18 found, 0 missing, 0 empty, 0 corrupted:  36%|###6      | 18/50 [00:00<00:00, 171.43it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-1' images and labels... 40 found, 0 missing, 0 empty, 0 corrupted:  80%|########  | 40/50 [00:00<00:00, 199.42it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-1' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 208.30it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   2%|1         | 19/1122 [00:02<01:11, 15.32it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   2%|1         | 21/1122 [00:02<01:14, 14.85it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   2%|2         | 23/1122 [00:02<01:10, 15.69it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   2%|2         | 26/1122 [00:02<01:03, 17.22it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   3%|2         | 29/1122 [00:02<00:58, 18.55it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   3%|2         | 32/1122 [00:02<00:56, 19.42it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:   3%|3         | 35/1122 [00:02<00:53, 20.

...

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-2' images and labels... 24 found, 0 missing, 0 empty, 0 corrupted:  48%|####8     | 24/50 [00:00<00:00, 230.77it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-2' images and labels... 48 found, 0 missing, 0 empty, 0 corrupted:  96%|#########6| 48/50 [00:00<00:00, 194.43it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-2' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 201.61it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 

C:\Experiments\ALFL

C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/50 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-3' images and labels... 27 found, 0 missing, 0 empty, 0 corrupted:  54%|#####4    | 27/50 [00:00<00:00, 259.54it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-fl-1epoch-feb24\l-3' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 50/50 [00:00<00:00, 251.26it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 1


C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.73, Best Possible Recall (BPR) = 0.9964
                 all        2244       12341    0.000521      0.0285    0.000194    3.97e-05
                 car        2244        8748     0.00383       0.144     0.00153    0.000314
             cyclist        2244         496    0.000121      0.0806    1.42e-05    2.56e-06
                misc        2244         293           0           0           0           0
          pedestrian        2244        1332           0           0           0           0
      person_sitting        2244          87           0           0           0           0
                tram        2244         154           0           0           0           0
               truck        2244         326           0           0           0           0
                 van        2244         905    0.000223     0.00331    4.65e-06    1.61e-06



               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  96%|#########5| 1074/1122 [00:55<00:02, 21.37it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  96%|#########5| 1077/1122 [00:55<00:02, 21.29it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  96%|#########6| 1080/1122 [00:55<00:01, 21.02it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  97%|#########6| 1083/1122 [00:55<00:01, 20.96it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  97%|#########6| 1086/1122 [00:55<00:01, 21.01it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  97%|#########7| 1089/1122 [00:55<00:01, 20.96it/s]
               Class      Images      Labels           P           R      mAP@.5  mAP@.5:.95:  97%|#########7| 1092/1122 [0

In [16]:
txt = ''
cp = txt.lower()=='cpu'
print(cp)

False


## Optimizer stripped - Taking last.pt from previous client

#### Centralized

In [16]:
!python research2.py --action train --epochs 1 --batch_size 15 --pretrain --client 0 --classes 8 --round 0 --name {cl_name}

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.72, Best Possible Recall (BPR) = 0.9972


C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-cl-rerun-m15\l-0.cache' images and labels... 60 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 60/60 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-cl-rerun-m15\l-0.cache' images and labels... 60 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 60/60 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it

#### Decentralized

In [17]:
for client in range(DEVICES):
        if client == 0:
            !python research2.py --action train --epochs 1 --batch_size 15 --pretrain --client 0 --classes 8 --round 0 --name {fl_name}
        else:
            weights = f'runs/run-{fl_name}-{client-1}-0/weights/last.pt'
            !python research2.py --action train --epochs 1 --batch_size 15 --weights {weights} --client {client} --classes 8 --round 0 --name {fl_name} 

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.66, Best Possible Recall (BPR) = 1.0000


C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-fl-rerun-m15\l-0.cache' images and labels... 15 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 15/15 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-fl-rerun-m15\l-0.cache' images and labels... 15 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 15/15 [00:00<?, ?it/s]

val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]
val: Scanning 'KITTI\flcl\val.cache' images and labels... 2244 found, 0 missing, 0 empty, 0 corrupted: 100%|##########| 2244/2244 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.62, Best Possible Recall (BPR) = 0.9868
Missing files. Existing are: weights: runs/run-fl-rerun-m15-1-0/weights/last.ptFalse, model: True, hyperparameters: True
Missing files. Existing are: weights: runs/run-fl-rerun-m15-2-0/weights/last.ptFalse, model: True, hyperparameters: True


In [31]:
for rd in range(2):
    for client in range(DEVICES):
        if client == 0 and rd == 0:
#             continue
#             print(f"Initial weights")
            !python research2.py --action train --epochs 1 --batch_size 15 --pretrain --client 0 --classes 8 --round {rd} --name flcl-fl-2epoch-last-mar9
        elif client ==0:
#             print(f"In Round {rd}, Client {client} uses client 3's weights from round {rd-1}")
            weights = f'runs/run-flcl-fl-2epoch-last-mar9-3-{rd-1}/weights/last.pt'
            !python research2.py --action train --epochs 1 --batch_size 15 --weights {weights} --client {client} --classes 8 --round {rd} --name flcl-fl-2epoch-last-mar9
        else:
#             print(f"In Round {rd}, Client {client} uses client {client-1}'s weights from round {rd}")
#             print(f"Round {rd}, Client-1 {client-1}")
#             print()
            weights = f'runs/run-flcl-fl-2epoch-last-mar9-{client-1}-{rd}/weights/last.pt'
#             print(weights)
            !python research2.py --action train --epochs 1 --batch_size 15 --weights {weights} --client {client} --classes 8 --round {rd} --name flcl-fl-2epoch-last-mar9            

C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.66, Best Possible Recall (BPR) = 1.0000



wandb: Currently logged in as: dyeleshetty (use `wandb login --relogin` to force relogin)
wandb: Tracking run with wandb version 0.12.11
wandb: Run data is saved locally in C:\Experiments\ALFL\wandb\run-20220309_171826-3amsfryx
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run serene-donkey-57
wandb:  View project at https://wandb.ai/dyeleshetty/AccFL-1EpochTest
wandb:  View run at https://wandb.ai/dyeleshetty/AccFL-1EpochTest/runs/3amsfryx
wandb: WARNING Calling wandb.run.save without any arguments is deprecated.Changes to attributes are automatically persisted.
C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl-2epoch-last-mar9\l-0.cache' ima

C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.62, Best Possible Recall (BPR) = 0.9868



wandb: Currently logged in as: dyeleshetty (use `wandb login --relogin` to force relogin)
wandb: Tracking run with wandb version 0.12.11
wandb: Run data is saved locally in C:\Experiments\ALFL\wandb\run-20220309_171853-1xcyex5b
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run visionary-haze-58
wandb:  View project at https://wandb.ai/dyeleshetty/AccFL-1EpochTest
wandb:  View run at https://wandb.ai/dyeleshetty/AccFL-1EpochTest/runs/1xcyex5b
wandb: WARNING Calling wandb.run.save without any arguments is deprecated.Changes to attributes are automatically persisted.
C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl-2epoch-last-mar9\l-1.cache' im

Missing files. Existing are: weights: runs/run-flcl-fl-2epoch-last-mar9-1-0/weights/last.ptFalse, model: True, hyperparameters: True



...

wandb: Currently logged in as: dyeleshetty (use `wandb login --relogin` to force relogin)
wandb: Tracking run with wandb version 0.12.11
wandb: Run data is saved locally in C:\Experiments\ALFL\wandb\run-20220309_171949-6ol94ww8
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run scarlet-cloud-62
wandb:  View project at https://wandb.ai/dyeleshetty/AccFL-1EpochTest
wandb:  View run at https://wandb.ai/dyeleshetty/AccFL-1EpochTest/runs/6ol94ww8
wandb: WARNING Calling wandb.run.save without any arguments is deprecated.Changes to attributes are automatically persisted.
wandb: Waiting for W&B process to finish... (success).
wandb: - 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: \ 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: | 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: / 0.001 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: - 0.001 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: \ 0.004 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: | 0

Missing files. Existing are: weights: runs/run-flcl-fl-2epoch-last-mar9-1-1/weights/last.ptFalse, model: True, hyperparameters: True

wandb: Currently logged in as: dyeleshetty (use `wandb login --relogin` to force relogin)
wandb: Tracking run with wandb version 0.12.11
wandb: Run data is saved locally in C:\Experiments\ALFL\wandb\run-20220309_172002-385tj97y
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run leafy-fog-63
wandb:  View project at https://wandb.ai/dyeleshetty/AccFL-1EpochTest
wandb:  View run at https://wandb.ai/dyeleshetty/AccFL-1EpochTest/runs/385tj97y
wandb: WARNING Calling wandb.run.save without any arguments is deprecated.Changes to attributes are automatically persisted.
wandb: Waiting for W&B process to finish... (success).
wandb: - 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: \ 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: | 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: / 0.001 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: - 0.001 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: \ 0.001 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: | 0.004



Missing files. Existing are: weights: runs/run-flcl-fl-2epoch-last-mar9-2-1/weights/last.ptFalse, model: True, hyperparameters: True



wandb: Currently logged in as: dyeleshetty (use `wandb login --relogin` to force relogin)
wandb: Tracking run with wandb version 0.12.11
wandb: Run data is saved locally in C:\Experiments\ALFL\wandb\run-20220309_172015-39cb8sb7
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run robust-firefly-64
wandb:  View project at https://wandb.ai/dyeleshetty/AccFL-1EpochTest
wandb:  View run at https://wandb.ai/dyeleshetty/AccFL-1EpochTest/runs/39cb8sb7
wandb: WARNING Calling wandb.run.save without any arguments is deprecated.Changes to attributes are automatically persisted.
wandb: Waiting for W&B process to finish... (success).
wandb: - 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: \ 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: | 0.001 MB of 0.001 MB uploaded (0.000 MB deduped)
wandb: / 0.001 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: - 0.001 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: \ 0.004 MB of 0.004 MB uploaded (0.000 MB deduped)
wandb: | 

In [35]:
!python research2.py --action train --epochs 1 --batch_size 15 --pretrain --client 0 --classes 8 --round 0 --name flcl-fl-2epoch-last-mar9

C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.66, Best Possible Recall (BPR) = 1.0000



wandb: Currently logged in as: dyeleshetty (use `wandb login --relogin` to force relogin)
wandb: Tracking run with wandb version 0.12.11
wandb: Run data is saved locally in C:\Experiments\ALFL\wandb\run-20220309_173434-3fi1i8fg
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run elated-wood-67
wandb:  View project at https://wandb.ai/dyeleshetty/AccFL-1EpochTest
wandb:  View run at https://wandb.ai/dyeleshetty/AccFL-1EpochTest/runs/3fi1i8fg
wandb: WARNING Calling wandb.run.save without any arguments is deprecated.Changes to attributes are automatically persisted.
C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl-2epoch-last-mar9\l-0.cache' image

In [37]:
weights = f'runs/run-flcl-fl-2epoch-last-mar9-0-0/weights/last.pt'
!python research2.py --action train --epochs 1 --batch_size 15 --weights {weights} --client 1 --classes 8 --round 0 --name flcl-fl-2epoch-last-mar9

C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.62, Best Possible Recall (BPR) = 0.9868



wandb: Currently logged in as: dyeleshetty (use `wandb login --relogin` to force relogin)
wandb: Tracking run with wandb version 0.12.11
wandb: Run data is saved locally in C:\Experiments\ALFL\wandb\run-20220309_174014-1dca31b3
wandb: Run `wandb offline` to turn off syncing.
wandb: Syncing run fancy-glitter-69
wandb:  View project at https://wandb.ai/dyeleshetty/AccFL-1EpochTest
wandb:  View run at https://wandb.ai/dyeleshetty/AccFL-1EpochTest/runs/1dca31b3
wandb: WARNING Calling wandb.run.save without any arguments is deprecated.Changes to attributes are automatically persisted.
C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

train: Scanning 'KITTI\flcl\clients\run-flcl-fl-2epoch-last-mar9\l-1.cache' ima

## BatchSize=50

In [6]:
!python research2.py --action train --epochs 1 --batch_size 50 --pretrain --client 0 --classes 8 --round 0 --test --name flcl-cl-1epoch-feb25

C:\Experiments\ALFL
C:\Experiments\ALFL

autoanchor: Analyzing anchors... anchors/target = 4.79, Best Possible Recall (BPR) = 0.9981


C:\Users\YeleshettyD\Anaconda3\envs\AccFL\lib\site-packages\torch\functional.py:445: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  ..\aten\src\ATen\native\TensorShape.cpp:2157.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]

Scanning images:   0%|          | 0/200 [00:00<?, ?it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb25\l-0' images and labels... 15 found, 0 missing, 0 empty, 0 corrupted:   8%|7         | 15/200 [00:00<00:01, 144.19it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb25\l-0' images and labels... 33 found, 0 missing, 0 empty, 0 corrupted:  16%|#6        | 33/200 [00:00<00:01, 160.54it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb25\l-0' images and labels... 50 found, 0 missing, 0 empty, 0 corrupted:  25%|##5       | 50/200 [00:00<00:00, 164.33it/s]
train: Scanning 'KITTI\flcl\clients\run-flcl-cl-1epoch-feb25\l-0' ima